In [1]:
# ========= Imports and Data Loading ========= #
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset, Dataset

import numpy as np
import pandas as pd

import re

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

import nltk
from nltk.tokenize import word_tokenize

import matplotlib.pyplot as plt

import numpy as np
import pandas as pd
import re
import string                             

!pip install tashaphyne
import tashaphyne
from tashaphyne.stemming import ArabicLightStemmer

!pip install pyarabic
import pyarabic

!pip install emoji
import emoji

import nltk                             
from nltk.stem.isri import ISRIStemmer
from nltk.corpus import stopwords 
nltk.download('stopwords')                                
nltk.download('punkt')


from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn import svm
from sklearn import metrics
from sklearn import naive_bayes
from sklearn.metrics import f1_score

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


[nltk_data] Downloading package stopwords to /home/ahmed/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/ahmed/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
# read csv file
def load_data(path):
    df = pd.read_csv(path, encoding='UTF-8')
    return  np.asarray(df['text'].values), np.asarray(df['category'].values), np.asarray(df['stance'].values)

train_tweets, train_categories, train_stances = load_data('Dataset/train.csv')
dev_tweets, dev_categories, dev_stances = load_data('Dataset/dev.csv')

In [3]:
def preprocess_tweet(tweet):
    ArListem = ArabicLightStemmer()

    def stem_tweet(tweet_tokens):
        for i in range(len(tweet_tokens)):
            ArListem.light_stem(tweet_tokens[i])
            tweet_tokens[i] = ArListem.get_root()
        return tweet_tokens

    def remove_url(tweet):
        tweet = re.sub(r"http\S+", " ", tweet)
        return tweet

    def remove_retweet_tag(tweet):
        tweet = re.sub(r'^RT[\s]+', ' ', tweet)
        return tweet

    def remove_tweet_mentions(tweet):
        tweet = re.sub(r'@\w+', ' ', tweet)
        return tweet

    def remove_text_control_tags(tweet):
        tweet = re.sub(r'\n|\t|\r|<LF>|<lf>', ' ', tweet)
        return tweet

    def tokenize_tweet(tweet):
        tweet_tokens = re.split(r',|،|_|-|!| ', tweet)
        return tweet_tokens

    def remove_stopwords_punctuation(tweet_tokens, stop_words = ()):
        tweet_reduced = []
        for word in tweet_tokens:
            if (word not in stop_words and word not in string.punctuation):
                tweet_reduced.append(word)
                tweet_reduced[-1] = re.sub(r'[~`!@#$%^&*()-/_+={}[\]|/\:;"`<>,.?؟،]+', ' ', tweet_reduced[-1])
        return tweet_reduced

    def remove_specialcharacters(tweet):
        tweet = re.sub(r'#', ' ', tweet)
        return tweet

    def handle_emojis(tweet, remove_emojis = True):
        if not remove_emojis:
            tweet = emoji.demojize(tweet, language='en') # convert emojis to text ENGLISH!!
        else:
            for e in tweet:
                if emoji.is_emoji(e):
                   tweet = tweet.replace(e, '')
        return tweet

    def normalize_tweet(tweet_tokens):
        for i in range(len(tweet_tokens)):
            tweet_tokens[i] = pyarabic.araby.strip_tashkeel(tweet_tokens[i])
            tweet_tokens[i] = pyarabic.araby.strip_tatweel(tweet_tokens[i])
            tweet_tokens[i] = pyarabic.araby.strip_lastharaka(tweet_tokens[i])
            tweet_tokens[i] = re.sub(r'(.)\1{3,}', r"\1\1\1", tweet_tokens[i]) # Remove longation
            # tweet_tokens[i] = pyarabic.araby.normalize_alef(tweet_tokens[i])
            # tweet_tokens[i] = pyarabic.araby.normalize_hamza(tweet_tokens[i])
        return tweet_tokens

    tweet = remove_url(tweet)
    tweet = remove_retweet_tag(tweet)
    tweet = remove_specialcharacters(tweet)
    tweet = remove_text_control_tags(tweet)
    tweet = remove_tweet_mentions(tweet)
    tweet = handle_emojis(tweet, remove_emojis = True)
    tweet_tokens = tokenize_tweet(tweet)
    # tweet_tokens = normalize_tweet(tweet_tokens)
    tweet_tokens = remove_stopwords_punctuation(tweet_tokens, stopwords.words('arabic'))
    # tweet_tokens = stem_tweet(tweet_tokens)
    tweet = ' '.join(tweet_tokens)
    tweet = re.sub(r'[^\w\s]+|\d+',' ',tweet)  # to remove non-printable characters and numbers
    tweet = re.sub(r'\s+', ' ', tweet)     # to remove multiple spaces
    return tweet

In [4]:
def tokenize(tweet):
    tweet = re.split(r' ', tweet)
    # print(tweet)
    tweet = [word for word in tweet if word != '']
    # print(tweet)
    return tweet
    
for i in range(len(train_tweets)):
    train_tweets[i] = tokenize(preprocess_tweet(train_tweets[i]))

for i in range(len(dev_tweets)):
    dev_tweets[i] = tokenize(preprocess_tweet(dev_tweets[i]))


['بيل', 'غيتس', 'يتلقى', 'لقاح', 'كوفيد', 'تصوير', 'الابرة', 'السيرنجة', 'الدواء', 'لابس', 'بولو', 'صيفي', 'عز', 'الشتاء', 'يقول', 'ان', 'مزايا', 'عمر', 'ال', 'عام', 'ا', 'انه', 'مؤهل', 'للحصول', 'اللقاح', 'يعنى', 'يحتاج', 'اللقاح', 'عمره', 'اصغر', '']
['بيل', 'غيتس', 'يتلقى', 'لقاح', 'كوفيد', 'تصوير', 'الابرة', 'السيرنجة', 'الدواء', 'لابس', 'بولو', 'صيفي', 'عز', 'الشتاء', 'يقول', 'ان', 'مزايا', 'عمر', 'ال', 'عام', 'ا', 'انه', 'مؤهل', 'للحصول', 'اللقاح', 'يعنى', 'يحتاج', 'اللقاح', 'عمره', 'اصغر']
['وزير', 'الصحة', 'لحد', 'اليوم', 'وتحديدا', 'هلأ', 'بمؤتمروا', 'الصحفي', 'عندي', 'مشكلة', 'معوا', 'انوا', 'بفايزر', 'اللقاح', 'الوحيد', 'الآمن', 'بالعالم', 'لأ', 'حبيبي', 'هاي', 'نفاق', 'واضح', 'عفوا', 'يعني', 'مش', 'إنوا', 'مجبورين', 'قادر', 'تجبر', 'الدولة', 'المارقة', 'تدفع', 'مصاري', 'تجيب', 'لقاح', 'تاني', 'يلا', 'باي']
['وزير', 'الصحة', 'لحد', 'اليوم', 'وتحديدا', 'هلأ', 'بمؤتمروا', 'الصحفي', 'عندي', 'مشكلة', 'معوا', 'انوا', 'بفايزر', 'اللقاح', 'الوحيد', 'الآمن', 'بالعالم', 'لأ', 'حبيبي'

In [5]:
# zip the tweets and categories and stances together
train_data = np.asarray((list(zip(train_categories, train_stances, train_tweets))))
dev_data = np.asarray((list(zip(dev_categories, dev_stances, dev_tweets))))

/tmp/ipykernel_29144/4134650653.py:2: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  train_data = np.asarray((list(zip(train_categories, train_stances, train_tweets))))
/tmp/ipykernel_29144/4134650653.py:3: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  dev_data = np.asarray((list(zip(dev_categories, dev_stances, dev_tweets))))


In [6]:
# print the shape of the first element in train_data
# print(train_data[0][0])
a, b, c = train_data[0]
print(a)
print(b)
print(c)

celebrity
1
['بيل', 'غيتس', 'يتلقى', 'لقاح', 'كوفيد', 'تصوير', 'الابرة', 'السيرنجة', 'الدواء', 'لابس', 'بولو', 'صيفي', 'عز', 'الشتاء', 'يقول', 'ان', 'مزايا', 'عمر', 'ال', 'عام', 'ا', 'انه', 'مؤهل', 'للحصول', 'اللقاح', 'يعنى', 'يحتاج', 'اللقاح', 'عمره', 'اصغر']


In [7]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [8]:
# class Preprocessing():
#     def __init__(self, train_path):
#         super().__init__()
        
#         self.train_df = self.load_data(train_path)
#         self.value_counts = self.train_df['stance'].value_counts()
        
#         self.train_set = list(self.train_df.to_records(index=False))
#         self.tokenizate()
        
#     def load_data(self, train_path):
#         return pd.read_csv(train_path)
    
#     def remove_links_mentions(self, tweet):
#         link_re_pattern = "https?:\/\/t.co/[\w]+"
#         mention_re_pattern = "@\w+"
#         tweet = re.sub(link_re_pattern, "", tweet)
#         tweet = re.sub(mention_re_pattern, "", tweet)
#         return tweet.lower()
    
#     def tokenizate(self):
#         self.train_set = [(category, label, word_tokenize(self.remove_links_mentions(tweet))) for (tweet, category, label) in self.train_set]
    
#     def get_datasets(self):
#         return self.train_set    

In [9]:
class TweetsDataset(Dataset):
    def __init__(self, train_set):
        super().__init__()
        self.train_set = train_set
                
        self.index2word = self.construct_index2word()
        self.voc_size = len(self.index2word)
        self.word2index = {token: idx for idx, token in enumerate(self.index2word)}

        self.max_seq_length = self.get_max_seq()
        self.train_encoded = [(category, label, self.encode_and_pad(tweet, self.max_seq_length)) for category, label, tweet in self.train_set]
        
        self.data = (np.array([tweet for category, label, tweet in self.train_encoded]))
        self.label = (np.array([label for category, label, tweet in self.train_encoded]))

        self.train_ds = TensorDataset(torch.from_numpy(self.data), torch.from_numpy(self.label))
        
#         Add Categories in train_ds
        
    def construct_index2word(self):
        index2word = ["<PAD>", "<SOS>", "<EOS>"]

        for ds in [self.train_set]:
            for category, label, tweet in ds:
                for token in tweet:
                    if token not in index2word:
                        index2word.append(token)
        return index2word
    
    def get_max_seq(self):
        max_seq_length = 0
        for tweet, category, label in self.train_set:
            if len(tweet) > max_seq_length:
                max_seq_length = len(tweet)
        return max_seq_length
    
    def encode_and_pad(self, tweet, length):
        sos = [self.word2index["<SOS>"]]
        eos = [self.word2index["<EOS>"]]
        pad = [self.word2index["<PAD>"]]

        if len(tweet) < length - 2: # -2 for SOS and EOS
            n_pads = length - 2 - len(tweet)
            encoded = [self.word2index[w] for w in tweet]
            return sos + encoded + eos + pad * n_pads 
        else: # tweet is longer than possible; truncating
            encoded = [self.word2index[w] for w in tweet]
            truncated = encoded[:length - 2]
            return sos + truncated + eos
    
    def get_data(self):
        return self.train_ds

In [10]:
class RNN(nn.Module):
    def __init__(self, vocab_size, embedding_dim, hidden_size, num_layers, num_classes):
        super(RNN, self).__init__()
        self.num_layers = num_layers
        self.hidden_size = hidden_size
        self.vocab_size = vocab_size
        
        self.embedding_size = embedding_dim
        self.embedding = nn.Embedding(vocab_size, embedding_dim=embedding_dim, padding_idx=0)
        
        self.rnn = nn.RNN(embedding_dim, hidden_size, num_layers, batch_first=True)
        self.fc = nn.Linear(hidden_size, num_classes)

    def forward(self, input):
        input = self.embedding(torch.tensor(input))
        out, _ = self.rnn(input)
        out = out[:, -1, :]
        out = self.fc(out)
        return out

In [11]:
class RnnTweetsClassifier():
    def __init__(self, dataset, embedding_dim, hidden_size, num_layers, num_classes, epoch_size, learning_rate):
        self.dataset = dataset
        self.embedding_dim = embedding_dim
        self.epoch_size = epoch_size
        self.learning_rate = learning_rate
        self.model = RNN(dataset.voc_size, embedding_dim, hidden_size, num_layers, num_classes)
        self.data_loader = DataLoader(dataset=dataset.get_data(), batch_size=256, shuffle=True)
        self.criterion = nn.CrossEntropyLoss()
        self.optimizer = torch.optim.Adam(self.model.parameters(), self.learning_rate)
         
    def train(self):
        for epoch in range(self.epoch_size):
            total_model_acc = 0
            for data in self.data_loader:
                train_data = data[:][0]
                labels = data[:][1]
                # reshape the row data
                output = self.model(train_data)
                # calculate the accuracy
                total_model_acc += (torch.argmax(output, dim=1) == (labels + 1)).sum()
                loss = self.criterion(output, (labels + 1))
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()

            total_model_acc = total_model_acc / len(self.dataset.get_data())
            print(f"epoch num: {epoch} has accuracy: {total_model_acc}")

    def predict(self, testLoader):
        with torch.no_grad():
            n_correct = 0
            n_samples = 0
            for tweets in testLoader:
                test_data = tweets[:][0]
                labels = tweets[:][1]
                output = self.model(test_data)
                n_correct += (torch.argmax(output, dim=1) == (labels + 1)).sum()
                n_samples += labels.size(0)
            print(f"Model accuracy: {100 * n_correct / n_samples}")
            print("Model F1 Score: ",f1_score(labels, torch.argmax(output,dim=1), average="macro"))

In [13]:
# =========== Training =========== #
dataset = TweetsDataset(train_data)
tweet_classifier = RnnTweetsClassifier(dataset, 50, 50, 1, 3, 7, 0.001)
tweet_classifier.train()

/tmp/ipykernel_29144/1089490090.py:15: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input = self.embedding(torch.tensor(input))


epoch num: 0 has accuracy: 0.7786204814910889
epoch num: 1 has accuracy: 0.7925014495849609
epoch num: 2 has accuracy: 0.7923583388328552
epoch num: 3 has accuracy: 0.7936462759971619
epoch num: 4 has accuracy: 0.8008013963699341
epoch num: 5 has accuracy: 0.8072409629821777
epoch num: 6 has accuracy: 0.8175443410873413


In [15]:
# =========== Test =========== #
# dev_path = "./dataset/dev.csv"
# preprocessing = Preprocessing(dev_path)
# dev = preprocessing.get_datasets()
testset = TweetsDataset(dev_data)
testloader = DataLoader(dataset=testset.get_data(), batch_size=256, shuffle=True)
tweet_classifier.predict(testloader)

Model accuracy: 74.5
Model F1 Score:  0.050275373721479145


/tmp/ipykernel_29144/1089490090.py:15: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input = self.embedding(torch.tensor(input))
